In [1]:
# making use of libraries from https://github.com/ComparativeGenomicsToolkit/Comparative-Annotation-Toolkit
# this script also requires the bx-python library as well as the hal2maf program in the haltools
from tools.transcripts import *
import pandas as pd
from multiprocessing import Pool
from tools.bio import *
from tools.intervals import *
from tools.mathOps import *
from tools.fileOps import *
from tools.dataOps import *
from glob import glob
import bx.align.maf

In [2]:
# input files
# deletion_bed is a BED in Clint coordinates marking intervals of human-specific deletion
deletion_bed = 'human_specific_insertions.0.8.no-lineage-specific.chimp.bed'

# chimp_genome_sizes is a tab delimited file of [contig, contig_length] pairs
chimp_genome_sizes = 'Clint_Chimp.chrom.sizes'

# hcondel_hal is a cactus alignment of Clint, rheMac8, mm10, goat, and galGal4
hcondel_hal = 'hcondel.hal'

In [4]:
# extract MAF for just the loci of interest
# Use a 100bp buffer around each, so load chrom sizes

sizes = dict(x.split() for x in open(chimp_genome_sizes))

# construct commands
!mkdir hcondel_maf -p
base_cmd = 'hal2maf {} --refGenome Chimp --targetGenomes Chimp,Mouse,Rhesus --onlyOrthologs --noAncestors '
base_cmd = base_cmd.format(hcondel_hal)
with open('cmds.txt', 'w') as outf:
    for l in open(deletion_bed):
        l = l.split()
        chrom = l[0]
        chrom_size = int(sizes[chrom])
        start = max(int(l[1]) - 100, 0)
        stop = min(int(l[2]) + 100, chrom_size)
        length = stop - start
        maf = os.path.join('hcondel_maf', '{}_{}_{}.maf'.format(chrom, start, stop))
        cmd = base_cmd + ' --refSequence {} --start {} --length {} {}\n'.format(chrom, start, length, maf)
        outf.write(cmd)
        
# run on the cluster
path = os.getcwd()
!ssh ku 'cd {path}; para freeBatch; para make -ram=8g cmds.txt'

Told hub to free all batch-related resources
Batch not found.
Checking input files
7400 jobs written to /hive/groups/recon/projs/primates/hcondel_analysis/final_analysis/batch
7400 jobs in batch
0 jobs (including everybody's) in Parasol queue or running.
Checking finished jobs
updated job database on disk
Pushed Jobs: 7400
Checking job status 0 minutes after launch
7400 jobs in batch
6011 jobs (including everybody's) in Parasol queue or running.
Checking finished jobs
updated job database on disk
Checking job status 1 minutes after launch
7400 jobs in batch
0 jobs (including everybody's) in Parasol queue or running.
Checking finished jobs
updated job database on disk
Successful batch!


In [5]:
def sliding_window(l, step=1, window_size=50):
    """Iterator yielding sliding windows"""
    for i in xrange(0, l - window_size + 1, step):
        yield i, i + window_size


def parse_maf(maf, window_size=50, step=1, identity_cutoff=0.9, merge_distance=5):
    """
    Uses the bx python MAF parser to iterate over MAF columns, measuring identity in sliding windows.
    
    Nearby windows within merge_distance are merged after all windows are found.
    """
    maf_reader = bx.align.maf.Reader(open(maf))
    matches = []
    # store first component to keep track of chromosome name and alignment start position
    # first component in a MAF is always the reference genome
    # we have to use this instead of the location in case the alignment doesn't start at the same place
    first_comp = None  
    for m in maf_reader:
        comp = m.components[0]
        if first_comp is None:
            first_comp = comp
        # maintain mapping of components to genomes
        # this allows for discovery of duplicates in a genome to mask out
        species_map = {i: c.src.split('.')[0] for i, c in enumerate(m.components)}
        species = set(species_map.values())
        for i, column in enumerate(m.column_iter()):
            # mask out duplicated columns or columns without all 3 genomes
            if len(species) != 3 or len(species_map) != len(species):
                matches.append(0)
            elif len(set(x.upper() for x in column)) == 1:
                matches.append(1)
            else:
                matches.append(0)
    useful_windows = []
    for start, stop in sliding_window(len(matches), step, window_size):
        v = sum(matches[start:stop])
        ident = format_ratio(v, window_size)
        if ident >= identity_cutoff:
            useful_windows.append(ChromosomeInterval(first_comp.src, first_comp.start + start, first_comp.start + stop, '.'))
    return gap_merge_intervals(useful_windows, merge_distance)

In [6]:
# use the above functions on every maf extracted, finding windows of identity
r = []
hcondel_mafs = glob('hcondel_maf/*')
for window_size, identity in zip(*[[100, 50, 25], [0.9, 0.9, 0.92]]):
    vals = []
    for maf in hcondel_mafs:
        vals.append([maf, parse_maf(maf, window_size=window_size, identity_cutoff=identity)])
    r.append([window_size, identity, vals])

In [7]:
# convert these extracted windows to a output report DataFrame as well as a BED
munged = []
# report also on the total # of hsDEL with any
for window_size, identity, vals in r:
    matching_bases = int(window_size * identity)
    num_hcondel = 0
    window_coverage = 0
    num_windows = 0
    with open('hCONDEL_unfiltered_{}_window_{}_matching.bed'.format(window_size, matching_bases), 'w') as outf:
        for maf, v in vals:
            if len(v) > 0:
                num_hcondel += 1
            for interval in v:
                window_coverage += len(interval)
                num_windows += 1
                # strip MAF species identifier from chromosome names
                print_row(outf, [interval.chromosome.split('.')[1], interval.start, interval.stop])
    munged.append([window_size, matching_bases, num_hcondel, num_windows, window_coverage])
munged_df = pd.DataFrame(munged, columns=['Window size', '# matching bases', '# hCONDEL identified', '# windows identified', 'total bases'])
munged_df.head()

Window size  # matching bases  # hCONDEL identified  # windows identified  \
0          100                90                   175                   198   
1           50                45                   427                   580   
2           25                23                  1053                  2124   

   total bases  
0        31175  
1        55110  
2        94245

In [5]:
# we need to filter these by the actual hsDEL windows to ensure we aren't calling conservation in the flank
for window_size, identity in zip(*[[100, 50, 25], [0.9, 0.9, 0.92]]):
    matching_bases = int(window_size * identity)
    f = 'hCONDEL_unfiltered_{}_window_{}_matching.bed'.format(window_size, matching_bases)
    print window_size, identity
    !bedtools intersect -u -a {deletion_bed} -b {f} | wc -l

100 0.9
174
50 0.9
392
25 0.92
930


In [8]:
# report on how many of these loci are mappable to all 3 genomes, i.e. ones that could be considered to begin with
c = Counter()
for maf in hcondel_mafs:
    seen_genomes = set()
    maf_reader = bx.align.maf.Reader(open(maf))
    for m in maf_reader:
        species = {c.src.split('.')[0] for c in m.components}
        seen_genomes.update(species)
    c[frozenset(seen_genomes)] += 1
print c

Counter({frozenset(['Rhesus', 'Chimp', 'Mouse']): 4125, frozenset(['Rhesus', 'Chimp']): 2957, frozenset(['Chimp']): 285, frozenset(['Chimp', 'Mouse']): 33})
